In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import networkx as nx
import scipy

C:\Users\jgore\AppData\Local\Temp\ipykernel_1312\1987556014.py:1: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [12]:
# Read the CSV file into a pandas DataFrame
df = pd.read_csv('test_lineage_2.csv')

# Initialize a directed graph
G = nx.DiGraph()

# Iterate through the DataFrame
for index, row in df.iterrows():
    accession = row['Accession']
    in_collection = row['InCollection']
    
    # Assign a color based on the InCollection status
    node_color = 'blue' if in_collection else 'red'
    
    # Add node with the 'in_collection' attribute and assigned color
    G.add_node(accession, in_collection=in_collection, color=node_color)

    # Check for and add clone relationship
    clone_accession = row['CloneAccession']
    if pd.notna(clone_accession):
        # Assume clones have the same InCollection status as the original
        G.add_node(clone_accession, in_collection=in_collection, color=node_color)
        G.add_edge(accession, clone_accession, relationship='clone')

    # Check for and add maternal parent relationship
    maternal_parent = row['ParentAccession']
    if pd.notna(maternal_parent):
        # Maternal parent color needs to be determined the same way
        parent_in_collection = df[df['Accession'] == maternal_parent]['InCollection'].iloc[0]
        parent_color = 'blue' if parent_in_collection else 'red'
        G.add_node(maternal_parent, in_collection=parent_in_collection, color=parent_color)
        G.add_edge(maternal_parent, accession, relationship='parent')

# Use a layout that can be tweaked for a hierarchical look
#pos = nx.kamada_kawai_layout(G)
pos = nx.spring_layout(G, scale=2)

# Plotting the graph
plt.figure(figsize=(100, 100))

# Draw nodes with the color assigned based on InCollection status
node_colors = [G.nodes[node]['color'] for node in G]

# Calculate node degrees and scale them for the node size
# You can adjust the scale factor to control the node size differences
degree_dict = dict(G.degree(G.nodes()))
min_size = 1000  # Minimum size of node
size_factor = 1000  # Factor to scale by degree. You can adjust this for better sizing
node_sizes = [min_size + size_factor*degree_dict[node] for node in G.nodes()]

# Draw nodes with size based on degree
nx.draw_networkx_nodes(G, pos, node_size=node_sizes, node_color=node_colors)

# Draw edges
#nx.draw_networkx_edges(G, pos, edgelist=G.edges(), arrowstyle='->', arrowsize=20, edge_color='gray')
# Draw edges with different styles and arrows
for edge in G.edges(data=True):
    style = 'dotted' if edge[2]['relationship'] == 'clone' else 'solid'
    width = 1 if edge[2]['relationship'] == 'clone' else 2
    color = 'blue' if edge[2]['relationship'] == 'clone' else 'black'
    nx.draw_networkx_edges(G, pos, edgelist=[edge], arrowstyle='->', arrowsize=30, style=style, width=width, edge_color=color)

# Offset for labels above the nodes
label_pos = {key: [value[0], value[1] + 0.1] for key, value in pos.items()}  # Increase 0.1 or more if needed

# Draw labels offset above the nodes
#nx.draw_networkx_labels(G, label_pos, font_size=10, font_weight='bold')

plt.title('Family Tree')
plt.show()